# **앙상블 영어 감정분석 모델**

본 영어 감정분석 모델은 고려대학교 디지털금융공학과 DFE610 디지털금융공학을 위한 자연어처리기술 수업의 과제를 수행하기 위해 개발한 모델이다.

본 앙상블 영어 감정분석 모델은 ELECTRA 모델과 '네이버 영화리뷰 감정분석 with Hugging Face BERT' 모델을 오픈소스를 참고하여 구성하였다.

본 모델은 ELECTRA, BERT의 아웃풋을 Soft Voting하여 최종 아웃풋을 산출한다.


1.   모델의 오픈소스 참고 출처
- 모델의 오픈소스 참고 출처

    @ ELECTRA를 이용한 감정분석 모델 : https://github.com/jiwonny/nlp_emotion_classification

    @ 네이버 영화리뷰 감정분석 with Hugging Face BERT : https://colab.research.google.com/drive/13AMh8N9tEIw5rmxgc1fQfS8581mWegxj


2. 상세사항
- 아래 깃허브의 Readme.md 확인

  https://github.com/yklove1025/Ensamble-Sentiment-Analysis-for-Korean

3. 실행환경
- 본 소스는 구글 Colab에서 작성됨 
- 본 소스의 실행을 위해서는 Colab Pro 환경이 필요(GPU 메모리 필요)
- ① 실행 후 ② 순차 실행 → 종료 후 ③ 실행 (실행순번 표기)
- BERT 모델 저장 후 업로드 시에도 메모리 문제 발생 가능함(재실행 권장)

☞ Kaggle 리더보드에는 ELECTRA, BERT, Ensemble 각각 업로드 함

**☞ Kaggle 리더보드 업로드 시 index 칼럼명을 'Id'로 입력하여 저장 후 제출함**


**Hugging Face의 Transformer Model 설치 ①**

In [2]:
!pip install transformers

     |████████████████████████████████| 1.5MB 5.6MB/s 
     |████████████████████████████████| 890kB 15.8MB/s 
     |████████████████████████████████| 2.9MB 38.6MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893261 sha256=660418ba7b1c1918c7b0ca32526965647aeaf975c05082d038486291c9bdd031
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses


**학습 데이터 - 트레이닝/테스트 파일 업로드 ①**

In [3]:
from google.colab import files
files.upload()
# Friends training, dev, test 파일 로컬 pc에서 업로드

Saving friends_dev.json to friends_dev.json
Saving friends_test.json to friends_test.json
Saving friends_train.json to friends_train.json


{'friends_dev.json': b'[\n    [\n        {\n            "speaker": "Phoebe",\n            "utterance": "Oh my God, he\\u0092s lost it. He\\u0092s totally lost it.",\n            "emotion": "non-neutral",\n            "annotation": "0002120"\n        },\n        {\n            "speaker": "Monica",\n            "utterance": "What?",\n            "emotion": "surprise",\n            "annotation": "1000130"\n        },\n        {\n            "speaker": "Ross",\n            "utterance": "Or! Or, we could go to the bank, close our accounts and cut them off at the source.",\n            "emotion": "neutral",\n            "annotation": "3000200"\n        },\n        {\n            "speaker": "Chandler",\n            "utterance": "You\\u0092re a genius!",\n            "emotion": "joy",\n            "annotation": "0500000"\n        },\n        {\n            "speaker": "Joey",\n            "utterance": "Aww, man, now we won\\u0092t be bank buddies!",\n            "emotion": "sadness",\n         

**캐글 API 설정 ①**

In [4]:
!pip install kaggle
from google.colab import files
files.upload()
# 캐글 개인 API 토큰 파일 선택(kaggle.json)

Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"seungbumkim","key":"e78c5b15195059c492af320f88f3e880"}'}

In [5]:
ls -1ha kaggle.json

kaggle.json


In [6]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
# Permission Warning 이 일어나지 않도록 
!chmod 600 ~/.kaggle/kaggle.json

**캐글 테스트 데이터 다운로드 ①,②**

In [8]:
!kaggle competitions download -c english-sa-competition-dfe610
# 버젼 에러 발생할 경우 재실행

en_data.csv: Skipping, found more recently modified local copy (use --force to force download)


**공통 패키지 Import ①**

In [9]:
import pandas as pd
import numpy as np
import random
import time
import datetime
import torch
import tensorflow as tf
import keras
import os
import nltk
import matplotlib.pyplot as plt
import json
import re
 
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer
 
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
 
from sklearn.model_selection import train_test_split
from sklearn.ensemble import BaggingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score
 
from transformers import BertTokenizer
from transformers import ElectraTokenizer, ElectraForSequenceClassification
from transformers import BertForSequenceClassification, AdamW, BertConfig
from transformers import get_linear_schedule_with_warmup
 
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer
 
from keras.models import Sequential
from keras import layers
from keras.models import Model
from keras.models import load_model
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.layers.core import Dense, SpatialDropout1D 
from keras.layers.convolutional import Conv1D 
from keras.layers.embeddings import Embedding
from keras.layers.pooling import GlobalMaxPooling1D
from keras.layers import LSTM
from keras.models import Sequential 
from keras.utils import np_utils 
 
from nltk.corpus import stopwords
from nltk.tag import pos_tag
from nltk.tokenize import word_tokenize
from nltk import Text
 
import collections
 
from collections import OrderedDict
 
from pprint import pprint

**데이터 로드 ①** 

In [10]:
with open('./friends_train.json', encoding = 'utf-8', mode = 'r') as json_file:
    json_train = json.load(json_file)
with open('./friends_dev.json', encoding = 'utf-8', mode = 'r') as json_file:
    json_dev = json.load(json_file)
with open('./friends_test.json', encoding = 'utf-8', mode = 'r') as json_file:
    json_test = json.load(json_file)
 
print(json_train)
print(np.shape(json_train))
print(json_dev)
print(np.shape(json_dev))
print(json_test)
print(np.shape(json_test))

[[{'speaker': 'Chandler', 'utterance': 'also I was the point person on my company\x92s transition from the KL-5 to GR-6 system.', 'emotion': 'neutral', 'annotation': '4100000'}, {'speaker': 'The Interviewer', 'utterance': 'You must\x92ve had your hands full.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'That I did. That I did.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'The Interviewer', 'utterance': 'So let\x92s talk a little bit about your duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'My duties?  All right.', 'emotion': 'surprise', 'annotation': '2000030'}, {'speaker': 'The Interviewer', 'utterance': 'Now you\x92ll be heading a whole division, so you\x92ll have a lot of duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'I see.', 'emotion': 'neutral', 'annotation': '3100010'}, {'speaker': 'The Interviewer', 'utterance': 'But there\

/usr/local/lib/python3.6/dist-packages/numpy/core/_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)


In [11]:
kaggle = pd.read_csv("/content/en_data.csv", sep='\t', encoding = 'utf-8', delimiter = ',')
 
print(kaggle)

        id  ...                                          utterance
0        0  ...                      Alright, whadyou do with him?
1        1  ...                                  Oh! You're awake!
2        2  ...  Then you gotta come clean with Ma! This is not...
3        3  ...                                  Yeah, but this is
4        4  ...          I don't wanna hear it! Now go to my room!
...    ...  ...                                                ...
1618  1618  ...                                              Nooo.
1619  1619  ...                                          Hi, Kate!
1620  1620  ...                                        Hi, Lauren.
1621  1621  ...                                        Hi, Lauren.
1622  1622  ...                                           Hi, pig!

[1623 rows x 5 columns]


In [12]:
kaggle_data = []
 
kaggle_data = kaggle['utterance']
 
print(kaggle_data)

0                           Alright, whadyou do with him?
1                                       Oh! You're awake!
2       Then you gotta come clean with Ma! This is not...
3                                       Yeah, but this is
4               I don't wanna hear it! Now go to my room!
                              ...                        
1618                                                Nooo.
1619                                            Hi, Kate!
1620                                          Hi, Lauren.
1621                                          Hi, Lauren.
1622                                             Hi, pig!
Name: utterance, Length: 1623, dtype: object


**테스트, 트레이닝 변수 선언 ①**

In [13]:
train_data = []
test_data = []
kaggle_test =[]

**트레이닝, 테스트 데이터 클리닝 ①**

In [14]:
for rows in json_train:
    for row in rows:
        train_data.append(row)
for rows in json_dev:
    for row in rows:
        test_data.append(row)
for rows in json_test:
    for row in rows:
        train_data.append(row)
for rows in kaggle_data:
        kaggle_test.append(row)
 
print(train_data)
print(np.shape(train_data))
print(test_data)
print(np.shape(test_data))
print(kaggle_test)
print(np.shape(kaggle_data))

[{'speaker': 'Chandler', 'utterance': 'also I was the point person on my company\x92s transition from the KL-5 to GR-6 system.', 'emotion': 'neutral', 'annotation': '4100000'}, {'speaker': 'The Interviewer', 'utterance': 'You must\x92ve had your hands full.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'That I did. That I did.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'The Interviewer', 'utterance': 'So let\x92s talk a little bit about your duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'My duties?  All right.', 'emotion': 'surprise', 'annotation': '2000030'}, {'speaker': 'The Interviewer', 'utterance': 'Now you\x92ll be heading a whole division, so you\x92ll have a lot of duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'I see.', 'emotion': 'neutral', 'annotation': '3100010'}, {'speaker': 'The Interviewer', 'utterance': 'But there\x

**트레이닝, 테스트 데이터 문장만 추출 ①**

In [15]:
train = []
test = []

In [16]:
for sentences in train_data :
  train.append(sentences['utterance'])
 
print(train[:5])
print(np.shape(train))

['also I was the point person on my company\x92s transition from the KL-5 to GR-6 system.', 'You must\x92ve had your hands full.', 'That I did. That I did.', 'So let\x92s talk a little bit about your duties.', 'My duties?  All right.']
(13325,)


In [17]:
for sentences in test_data :
  test.append(sentences['utterance'])
 
print(test[:5])
print(np.shape(test))

['Oh my God, he\x92s lost it. He\x92s totally lost it.', 'What?', 'Or! Or, we could go to the bank, close our accounts and cut them off at the source.', 'You\x92re a genius!', 'Aww, man, now we won\x92t be bank buddies!']
(1178,)


In [18]:
kaggle_sent = kaggle_data.tolist()
 
print(kaggle_sent[:5])
print(np.shape(kaggle_sent))

['Alright, whadyou do with him?', "Oh! You're awake!", 'Then you gotta come clean with Ma! This is not right!', 'Yeah, but this is', "I don't wanna hear it! Now go to my room!"]
(1623,)


**ELECTRA, BERT 텍스트 전처리 ①**

In [19]:
sentences = train
 
X_train_bert_in = ["[CLS] " + str(sentence) + " [SEP]" for sentence in sentences]
X_train_bert_in[:10]

['[CLS] also I was the point person on my company\x92s transition from the KL-5 to GR-6 system. [SEP]',
 '[CLS] You must\x92ve had your hands full. [SEP]',
 '[CLS] That I did. That I did. [SEP]',
 '[CLS] So let\x92s talk a little bit about your duties. [SEP]',
 '[CLS] My duties?  All right. [SEP]',
 '[CLS] Now you\x92ll be heading a whole division, so you\x92ll have a lot of duties. [SEP]',
 '[CLS] I see. [SEP]',
 '[CLS] But there\x92ll be perhaps 30 people under you so you can dump a certain amount on them. [SEP]',
 '[CLS] Good to know. [SEP]',
 '[CLS] We can go into detail [SEP]']

In [20]:
sentences = test
 
X_test_bert_in = ["[CLS] " + str(sentence) + " [SEP]" for sentence in sentences]
X_test_bert_in[:10]

['[CLS] Oh my God, he\x92s lost it. He\x92s totally lost it. [SEP]',
 '[CLS] What? [SEP]',
 '[CLS] Or! Or, we could go to the bank, close our accounts and cut them off at the source. [SEP]',
 '[CLS] You\x92re a genius! [SEP]',
 '[CLS] Aww, man, now we won\x92t be bank buddies! [SEP]',
 '[CLS] Now, there\x92s two reasons. [SEP]',
 '[CLS] Hey. [SEP]',
 '[CLS] Hey! [SEP]',
 '[CLS] Ohh, you guys, remember that cute client I told you about? I bit him. [SEP]',
 '[CLS] Where?! [SEP]']

In [21]:
sentences = kaggle_sent
 
kaggle_test_bert_in = ["[CLS] " + str(sentence) + " [SEP]" for sentence in sentences]
kaggle_test_bert_in[:10]

['[CLS] Alright, whadyou do with him? [SEP]',
 "[CLS] Oh! You're awake! [SEP]",
 '[CLS] Then you gotta come clean with Ma! This is not right! [SEP]',
 '[CLS] Yeah, but this is [SEP]',
 "[CLS] I don't wanna hear it! Now go to my room! [SEP]",
 '[CLS] I don?t want him to tell this story for years. [SEP]',
 '[CLS] Oh, but he will. He still tells the story how Monica tried to escape from fat camp. [SEP]',
 '[CLS] I wasn?t escaping. [SEP]',
 '[CLS] Then how did you get caught in the barbed wire? [SEP]',
 '[CLS] I was trying to help out a squirrel. [SEP]']

**레이블 처리 ①**

In [22]:
def labeltoint(str):
    return {'non-neutral': 0,
             'neutral': 1, 
             'joy': 2,
             'sadness': 3,
             'fear': 4,
             'anger': 5,
             'surprise': 6,
             'disgust': 7}[str]
 
labels_tr = []
labels_te = []
 
for d in train_data:
  labels_tr.append(labeltoint(d['emotion']))
 
 
for d in test_data:
  labels_te.append(labeltoint(d['emotion']))
 
print(labels_tr[:20])
print(labels_te[:20])

[1, 1, 1, 1, 6, 1, 1, 1, 1, 1, 4, 1, 6, 1, 6, 0, 6, 0, 1, 1]
[0, 6, 1, 2, 3, 1, 1, 2, 1, 6, 1, 1, 6, 0, 1, 2, 1, 1, 1, 6]


In [23]:
labels_train = np.array(labels_tr)
labels_test = np.array(labels_te)

In [24]:
print(labels_train)
print(labels_test)
print(len(labels_train))
print(len(labels_test))

[1 1 1 ... 1 1 1]
[0 6 1 ... 3 3 3]
13325
1178


**ELECTRA 감정분석 데이터 처리 ①**

In [25]:
tokenizer = ElectraTokenizer.from_pretrained('google/electra-large-discriminator')
#tokenizer = ElectraTokenizer.from_pretrained('google/electra-small-discriminator')
  
X_train_tokenized_text = [tokenizer.tokenize(sent) for sent in X_train_bert_in]
X_test_tokenized_text = [tokenizer.tokenize(sent) for sent in X_test_bert_in]
X_kaggle_tokenized_text = [tokenizer.tokenize(sent) for sent in kaggle_test_bert_in]
 
print (X_train_tokenized_text[0])
print (X_test_tokenized_text[0])
print (X_kaggle_tokenized_text[0])
 
MAX_LEN = 85
 
# 토큰을 숫자 인덱스로 변환
X_train_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_train_tokenized_text]
X_test_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_test_tokenized_text]
X_kaggle_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_kaggle_tokenized_text]
 
X_train_bert = pad_sequences(X_train_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
X_test_bert = pad_sequences(X_test_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
X_kaggle_bert = pad_sequences(X_kaggle_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")


['[CLS]', 'also', 'i', 'was', 'the', 'point', 'person', 'on', 'my', 'company', '##s', 'transition', 'from', 'the', 'k', '##l', '-', '5', 'to', 'gr', '-', '6', 'system', '.', '[SEP]']
['[CLS]', 'oh', 'my', 'god', ',', 'he', '##s', 'lost', 'it', '.', 'he', '##s', 'totally', 'lost', 'it', '.', '[SEP]']
['[CLS]', 'alright', ',', 'w', '##had', '##you', 'do', 'with', 'him', '?', '[SEP]']


**ELECTRA 감정분석 모델 설정 ①**

In [26]:
# 어텐션 마스크 초기화
attention_masks = []
 
# 어텐션 마스크를 패딩이 아니면 1, 패딩이면 0으로 설정
# 패딩 부분은 BERT 모델에서 어텐션을 수행하지 않아 속도 향상
for seq in X_train_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)
 
print(attention_masks[0])
 
# 훈련셋과 검증셋으로 분리
train_inputs, validation_inputs, train_labels, validation_labels = train_test_split(X_train_bert,
                                                                                    labels_train, 
                                                                                    random_state=2018, 
                                                                                    test_size=0.2)
 
# 어텐션 마스크를 훈련셋과 검증셋으로 분리
train_masks, validation_masks, _, _ = train_test_split(attention_masks, 
                                                       X_train_bert,
                                                       random_state=2018, 
                                                       test_size=0.2)
 
# 데이터를 파이토치의 텐서로 변환
train_inputs = torch.tensor(train_inputs)
train_labels = torch.tensor(train_labels)
train_masks = torch.tensor(train_masks)
validation_inputs = torch.tensor(validation_inputs)
validation_labels = torch.tensor(validation_labels)
validation_masks = torch.tensor(validation_masks)               
 
attention_masks = []
 
for seq in X_kaggle_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)
 
test_inputs = torch.tensor(X_kaggle_bert) 
test_masks = torch.tensor(attention_masks)

[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


In [27]:
# 배치 사이즈
batch_size = 32
 
# 파이토치의 DataLoader로 입력, 마스크, 라벨을 묶어 데이터 설정
# 학습시 배치 사이즈 만큼 데이터를 가져옴
train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)
 
validation_data = TensorDataset(validation_inputs, validation_masks, validation_labels)
validation_sampler = SequentialSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size=batch_size)

In [28]:
# GPU 디바이스 이름 구함
device_name = tf.test.gpu_device_name()
 
# GPU 디바이스 이름 검사
if device_name == '/device:GPU:0':
    print('Found GPU at: {}'.format(device_name))
else:
    raise SystemError('GPU device not found')

Found GPU at: /device:GPU:0


In [29]:
# 디바이스 설정
if torch.cuda.is_available():    
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    device = torch.device("cpu")
    print('No GPU available, using the CPU instead.')

There are 1 GPU(s) available.
We will use the GPU: Tesla P100-PCIE-16GB


In [30]:
# 분류를 위한 ELECTRA 모델 생성
#model = ElectraForSequenceClassification.from_pretrained('google/electra-large-generator', num_labels=8)
#model = ElectraForSequenceClassification.from_pretrained('google/electra-small-generator', num_labels=8)
model = ElectraForSequenceClassification.from_pretrained('google/electra-large-discriminator', num_labels=8)
model.cuda()

Some weights of the model checkpoint at google/electra-large-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at google/electra-large-discriminator and are newly initialized: ['classifier

ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(30522, 1024, padding_idx=0)
      (position_embeddings): Embedding(512, 1024)
      (token_type_embeddings): Embedding(2, 1024)
      (LayerNorm): LayerNorm((1024,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0): ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=1024, out_features=1024, bias=True)
              (key): Linear(in_features=1024, out_features=1024, bias=True)
              (value): Linear(in_features=1024, out_features=1024, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=1024, out_features=1024, bias=True)
              (LayerNorm

In [31]:
# 옵티마이저 설정
optimizer = AdamW(model.parameters(),
                  lr = 2e-5, 
                  eps = 1e-8
                )
 
epochs = 30
 
# 총 훈련 스텝 : 배치반복 횟수 * 에폭
total_steps = len(train_dataloader) * epochs
 
# 학습률을 조금씩 감소시키는 스케줄러 생성
scheduler = get_linear_schedule_with_warmup(optimizer, 
                                            num_warmup_steps = 0,
                                            num_training_steps = total_steps)

In [32]:
from sklearn.metrics import f1_score
 
# 정확도 계산 함수
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
 
    return np.sum(pred_flat == labels_flat) / len(labels_flat)
 
 
def getF1Score(preds, labels):
  pred_flat = np.argmax(preds, axis=1).flatten()
  labels_flat = labels.flatten()
 
  return f1_score(labels_flat, pred_flat, average = None)

In [33]:
# 시간 표시 함수
def format_time(elapsed):
 
    # 반올림
    elapsed_rounded = int(round((elapsed)))
    
    # hh:mm:ss으로 형태 변경
    return str(datetime.timedelta(seconds=elapsed_rounded))

**ELECTRA 감정분석 모델 학습 실행 ①**

In [34]:
seed_val = 42
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)
 
model.zero_grad()
 
# 에폭만큼 반복
for epoch_i in range(0, epochs):
    
    # ========================================
    #               Training
    # ========================================
    
    print("")
    print('======== Epoch {:} / {:} ========'.format(epoch_i + 1, epochs))
    print('Training...')
 
    t0 = time.time()
    total_loss = 0
    model.train()
        
    # 데이터로더에서 배치만큼 반복하여 가져옴
    for step, batch in enumerate(train_dataloader):
        if step % 500 == 0 and not step == 0:
            elapsed = format_time(time.time() - t0)
            print('  Batch {:>5,}  of  {:>5,}.    Elapsed: {:}.'.format(step, len(train_dataloader), elapsed))
 
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
             
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask, 
                        labels=b_labels)
 
        loss = outputs[0]
        total_loss += loss.item()
 
 
        loss.backward()
 
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()
        scheduler.step()
        model.zero_grad()
 
    # 평균 로스 계산
    avg_train_loss = total_loss / len(train_dataloader)            
 
    print("")
    print("  Average training loss: {0:.2f}".format(avg_train_loss))
    print("  Training epcoh took: {:}".format(format_time(time.time() - t0)))
        
    # ========================================
    #               Validation
    # ========================================
 
    print("")
    print("Running Validation...")
 
    t0 = time.time()
    model.eval()
    eval_loss, eval_accuracy, eval_f1 = 0, 0, 0
    nb_eval_steps, nb_eval_examples = 0, 0
 
    # 데이터로더에서 배치만큼 반복하여 가져옴
    for batch in validation_dataloader:
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
 
        with torch.no_grad():     
            outputs = model(b_input_ids, 
                            token_type_ids=None, 
                            attention_mask=b_input_mask)
        
        logits = outputs[0]
        logits = logits.detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()
     
        tmp_eval_accuracy = flat_accuracy(logits, label_ids)
        # tmp_eval_f1 = getF1Score(logits, label_ids)
        eval_accuracy += tmp_eval_accuracy
        # eval_f1 += tmp_eval_f1
        nb_eval_steps += 1
 
    print("  Accuracy: {0:.2f}".format(eval_accuracy/nb_eval_steps))
    # print("  F1: {0:.2f}".format(eval_f1/nb_eval_steps))
    print("  Validation took: {:}".format(format_time(time.time() - t0)))
 
print("")
print("Training complete!")


======== Epoch 1 / 30 ========
Training...

  Average training loss: 1.60
  Training epcoh took: 0:05:17

Running Validation...
  Accuracy: 0.47
  Validation took: 0:00:24

======== Epoch 2 / 30 ========
Training...

  Average training loss: 1.26
  Training epcoh took: 0:05:16

Running Validation...
  Accuracy: 0.60
  Validation took: 0:00:24

======== Epoch 3 / 30 ========
Training...

  Average training loss: 1.05
  Training epcoh took: 0:05:16

Running Validation...
  Accuracy: 0.61
  Validation took: 0:00:24

======== Epoch 4 / 30 ========
Training...

  Average training loss: 0.87
  Training epcoh took: 0:05:16

Running Validation...
  Accuracy: 0.61
  Validation took: 0:00:24

======== Epoch 5 / 30 ========
Training...

  Average training loss: 0.71
  Training epcoh took: 0:05:16

Running Validation...
  Accuracy: 0.63
  Validation took: 0:00:24

======== Epoch 6 / 30 ========
Training...

  Average training loss: 0.57
  Training epcoh took: 0:05:16

Running Validation...
  Accu

**ELECTRA 감정분석 모델 신규 텍스트 함수 선언 ①**

In [35]:
# 문장 테스트
def test_sentences(inputs, masks):
 
    # 평가모드로 변경
    model.eval()
 
    # 문장을 입력 데이터로 변환
    #inputs, masks = convert_input_data(sentences)
    inputs = inputs
    masks = masks
 
    # 데이터를 GPU에 넣음
    b_input_ids = inputs.to(device)
    b_input_mask = masks.to(device)
            
    # 그래디언트 계산 안함
    with torch.no_grad():     
        # Forward 수행
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask)
 
    # 로스 구함
    logits = outputs[0]
 
    # CPU로 데이터 이동
    logits = logits.detach().cpu().numpy()
 
    return logits

**ELECTRA를 이용한 감정분석 모델 테스트 Output 데이터 생성 ①**

- test 데이터 범위 지정 (GPU 사용량 관련 지정) ①

In [36]:
test_kaggle_inputs_1 = test_inputs[:1623]
test_kaggle_masks_1 = test_masks[:1623]

- Kaggle 테스트 데이터로 예측 수행 ①

In [37]:
logits = test_sentences(test_kaggle_inputs_1, test_kaggle_masks_1)
 
x_predict_ELECTRA = []
x_predict_ELECTRA = logits
 
x_predict_ELECTRA_socre = []
x_predict_ELECTRA_socre = np.argmax(logits, axis = 1)
x_predict_ELECTRA_score = x_predict_ELECTRA_socre.tolist()
 
print(x_predict_ELECTRA)
print(x_predict_ELECTRA_score)

[[-0.16522491  9.072702   -2.1876435  ... -1.5692517  -0.98051023
  -1.5804597 ]
 [-0.47574815 -1.1419594  -1.2472337  ... -1.2770699   7.603567
  -1.2807875 ]
 [ 4.024747   -3.2742553  -2.5440621  ...  6.0589743  -2.917479
   0.21478045]
 ...
 [-0.595267    9.256457   -1.0904887  ... -1.989375   -0.97649014
  -1.7918489 ]
 [-0.595267    9.256457   -1.0904887  ... -1.989375   -0.97649014
  -1.7918489 ]
 [ 8.382175   -1.811585   -0.43749875 ... -0.04149885 -2.321845
  -2.1107519 ]]
[1, 6, 5, 1, 5, 3, 1, 1, 6, 0, 5, 1, 0, 1, 6, 6, 3, 6, 0, 1, 1, 1, 6, 0, 2, 5, 5, 0, 5, 0, 4, 1, 7, 1, 1, 6, 1, 1, 6, 1, 1, 2, 6, 0, 1, 6, 3, 0, 1, 1, 1, 1, 1, 1, 1, 1, 6, 2, 3, 0, 2, 0, 0, 1, 1, 0, 1, 6, 5, 6, 0, 1, 1, 2, 1, 5, 0, 0, 6, 0, 0, 6, 1, 2, 6, 2, 2, 1, 1, 1, 1, 1, 1, 1, 5, 3, 1, 4, 1, 1, 1, 1, 1, 7, 6, 1, 4, 2, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 2, 0, 1, 5, 1, 2, 2, 0, 2, 2, 2, 1, 1, 0, 1, 6, 1, 0, 1, 1, 1, 1, 1, 2, 6, 6, 0, 0, 1, 6, 6, 1, 0, 1, 1, 1, 1, 1, 6, 1, 1, 0, 6, 0, 2, 6, 0, 0, 1, 1, 0, 6, 

- ELECTRA output csv 파일 저장 ①

In [38]:
ensemble_ELECTRA = pd.DataFrame(x_predict_ELECTRA)
print(ensemble_ELECTRA)

             0         1         2  ...         5         6         7
0    -0.165225  9.072702 -2.187644  ... -1.569252 -0.980510 -1.580460
1    -0.475748 -1.141959 -1.247234  ... -1.277070  7.603567 -1.280787
2     4.024747 -3.274255 -2.544062  ...  6.058974 -2.917479  0.214780
3    -0.310701  9.593419 -1.077573  ... -2.743481 -1.569642 -2.049925
4    -0.630141 -1.900750 -1.120545  ...  8.143746 -1.294476 -0.198117
...        ...       ...       ...  ...       ...       ...       ...
1618  4.083575 -0.439334 -3.954473  ... -2.378966 -1.429735  1.858148
1619 -0.481695 -0.882736  8.524299  ... -1.767983 -1.552010 -1.798602
1620 -0.595267  9.256457 -1.090489  ... -1.989375 -0.976490 -1.791849
1621 -0.595267  9.256457 -1.090489  ... -1.989375 -0.976490 -1.791849
1622  8.382175 -1.811585 -0.437499  ... -0.041499 -2.321845 -2.110752

[1623 rows x 8 columns]


In [39]:
ensemble_ELECTRA.to_csv('ensemble_ELECTRA_eng.csv')

- ELECTRA output 레이블 변환 파일 저장 ①

In [40]:
def inttolabel(str):
    return { 0 : 'non-neutral',
             1 : 'neutral', 
             2 : 'joy', 
             3 : 'sadness', 
             4 : 'fear', 
             5 : 'anger', 
             6 : 'surprise', 
             7 : 'disgust'}[str]
 
predicted_ELECTRA_str = []
 
for d in x_predict_ELECTRA_score:
  predicted_ELECTRA_str.append(inttolabel(d))

In [41]:
ensemble_ELECTRA_out = pd.DataFrame({'Expected' : predicted_ELECTRA_str})
print(ensemble_ELECTRA_out)

         Expected
0         neutral
1        surprise
2           anger
3         neutral
4           anger
...           ...
1618  non-neutral
1619          joy
1620      neutral
1621      neutral
1622  non-neutral

[1623 rows x 1 columns]


- Kaggle 리더보드 업로드 파일 생성 (csv 파일 변환 후 다운로드 하여 인덱스 칼럼명 'Id' 입력 필요)

In [42]:
ensemble_ELECTRA_out.to_csv('ensemble_ELECTRA_eng_score.csv')

**BERT 감정분석 데이터 처리 ②**

- 변수 초기화

In [43]:
X_train_tokenized_text = []
X_test_tokenized_text = []
X_kaggle_tokenized_text = []
X_train_bert = []
X_test_bert = []
X_kaggle_bert = []
train_inputs = []
train_labels = []
train_masks = []
validation_inputs = []
validation_labels = []
validation_masks = []
test_inputs = []
test_labels = []
test_masks = []

In [44]:
tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased', do_lower_case=False)
 
X_train_tokenized_text = [tokenizer.tokenize(sent) for sent in X_train_bert_in]
X_test_tokenized_text = [tokenizer.tokenize(sent) for sent in X_test_bert_in]
X_kaggle_tokenized_text = [tokenizer.tokenize(sent) for sent in kaggle_test_bert_in]
 
print (X_train_tokenized_text[0])
print (X_test_tokenized_text[0])
print (X_kaggle_tokenized_text[0])
 
# 입력 토큰의 최대 시퀀스 길이
MAX_LEN = 85
 
# 토큰을 숫자 인덱스로 변환
X_train_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_train_tokenized_text]
X_test_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_test_tokenized_text]
X_kaggle_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_kaggle_tokenized_text]
 
# 문장을 MAX_LEN 길이에 맞게 자르고, 모자란 부분을 패딩 0으로 채움
X_train_bert = pad_sequences(X_train_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
X_test_bert = pad_sequences(X_test_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
X_kaggle_bert = pad_sequences(X_kaggle_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")


['[CLS]', 'also', 'I', 'was', 'the', 'point', 'person', 'on', 'my', 'company', '##s', 'transition', 'from', 'the', 'K', '##L', '-', '5', 'to', 'GR', '-', '6', 'system', '.', '[SEP]']
['[CLS]', 'Oh', 'my', 'God', ',', 'he', '##s', 'lost', 'it', '.', 'He', '##s', 'totally', 'lost', 'it', '.', '[SEP]']
['[CLS]', 'Al', '##right', ',', 'w', '##had', '##yo', '##u', 'do', 'with', 'him', '?', '[SEP]']


**BERT 감정분석 모델 설정 ②**

In [45]:
# 어텐션 마스크 초기화
attention_masks = []
 
# 어텐션 마스크를 패딩이 아니면 1, 패딩이면 0으로 설정
# 패딩 부분은 BERT 모델에서 어텐션을 수행하지 않아 속도 향상
for seq in X_train_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)
 
print(attention_masks[0])
 
# 훈련셋과 검증셋으로 분리
train_inputs, validation_inputs, train_labels, validation_labels = train_test_split(X_train_bert,
                                                                                    labels_train, 
                                                                                    random_state=2018, 
                                                                                    test_size=0.1)
 
# 어텐션 마스크를 훈련셋과 검증셋으로 분리
train_masks, validation_masks, _, _ = train_test_split(attention_masks, 
                                                       X_train_bert,
                                                       random_state=2018, 
                                                       test_size=0.1)
 
# 데이터를 파이토치의 텐서로 변환
train_inputs = torch.tensor(train_inputs)
train_labels = torch.tensor(train_labels)
train_masks = torch.tensor(train_masks)
validation_inputs = torch.tensor(validation_inputs)
validation_labels = torch.tensor(validation_labels)
validation_masks = torch.tensor(validation_masks)               
 
attention_masks = []
 
for seq in X_kaggle_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)
 
test_inputs = torch.tensor(X_kaggle_bert)
test_masks = torch.tensor(attention_masks)

[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


In [46]:
# 배치 사이즈
batch_size = 32
 
# 파이토치의 DataLoader로 입력, 마스크, 라벨을 묶어 데이터 설정
# 학습시 배치 사이즈 만큼 데이터를 가져옴
train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)
 
validation_data = TensorDataset(validation_inputs, validation_masks, validation_labels)
validation_sampler = SequentialSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size=batch_size)

In [47]:
# GPU 디바이스 이름 구함
device_name = tf.test.gpu_device_name()
 
# GPU 디바이스 이름 검사
if device_name == '/device:GPU:0':
    print('Found GPU at: {}'.format(device_name))
else:
    raise SystemError('GPU device not found')

Found GPU at: /device:GPU:0


In [48]:
# 디바이스 설정
if torch.cuda.is_available():    
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    device = torch.device("cpu")
    print('No GPU available, using the CPU instead.')

There are 1 GPU(s) available.
We will use the GPU: Tesla P100-PCIE-16GB


In [49]:
# 분류를 위한 BERT 모델 생성
model = BertForSequenceClassification.from_pretrained("bert-base-multilingual-cased", num_labels=8)
model.cuda()

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model ch

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elemen

In [50]:
# 옵티마이저 설정
optimizer = AdamW(model.parameters(),
                  lr = 2e-5, # 학습률
                  eps = 1e-8 # 0으로 나누는 것을 방지하기 위한 epsilon 값
                )
 
# 에폭수
epochs = 10
 
# 총 훈련 스텝 : 배치반복 횟수 * 에폭
total_steps = len(train_dataloader) * epochs
 
# 처음에 학습률을 조금씩 변화시키는 스케줄러 생성
scheduler = get_linear_schedule_with_warmup(optimizer, 
                                            num_warmup_steps = 0,
                                            num_training_steps = total_steps)

In [51]:
from sklearn.metrics import f1_score
 
# 정확도 계산 함수
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
 
    return np.sum(pred_flat == labels_flat) / len(labels_flat)
 
 
def getF1Score(preds, labels):
  pred_flat = np.argmax(preds, axis=1).flatten()
  labels_flat = labels.flatten()
 
  return f1_score(labels_flat, pred_flat, average = None)

In [52]:
# 시간 표시 함수
def format_time(elapsed):
 
    # 반올림
    elapsed_rounded = int(round((elapsed)))
    
    # hh:mm:ss으로 형태 변경
    return str(datetime.timedelta(seconds=elapsed_rounded))

**BERT 감정분석 모델 학습 실행 ②**

In [53]:
seed_val = 42
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)
 
model.zero_grad()
 
# 에폭만큼 반복
for epoch_i in range(0, epochs):
    
    # ========================================
    #               Training
    # ========================================
    
    print("")
    print('======== Epoch {:} / {:} ========'.format(epoch_i + 1, epochs))
    print('Training...')
 
    t0 = time.time()
    total_loss = 0
    model.train()
        
    # 데이터로더에서 배치만큼 반복하여 가져옴
    for step, batch in enumerate(train_dataloader):
        if step % 500 == 0 and not step == 0:
            elapsed = format_time(time.time() - t0)
            print('  Batch {:>5,}  of  {:>5,}.    Elapsed: {:}.'.format(step, len(train_dataloader), elapsed))
 
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
             
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask, 
                        labels=b_labels)
 
        loss = outputs[0]
        total_loss += loss.item()
 
 
        loss.backward()
 
        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()
        scheduler.step()
        model.zero_grad()
 
    # 평균 로스 계산
    avg_train_loss = total_loss / len(train_dataloader)            
 
    print("")
    print("  Average training loss: {0:.2f}".format(avg_train_loss))
    print("  Training epcoh took: {:}".format(format_time(time.time() - t0)))
        
    # ========================================
    #               Validation
    # ========================================
 
    print("")
    print("Running Validation...")
 
    t0 = time.time()
    model.eval()
    eval_loss, eval_accuracy, eval_f1 = 0, 0, 0
    nb_eval_steps, nb_eval_examples = 0, 0
 
    # 데이터로더에서 배치만큼 반복하여 가져옴
    for batch in validation_dataloader:
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
 
        with torch.no_grad():     
            outputs = model(b_input_ids, 
                            token_type_ids=None, 
                            attention_mask=b_input_mask)
        
        logits = outputs[0]
        logits = logits.detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()
     
        tmp_eval_accuracy = flat_accuracy(logits, label_ids)
        # tmp_eval_f1 = getF1Score(logits, label_ids)
        eval_accuracy += tmp_eval_accuracy
        # eval_f1 += tmp_eval_f1
        nb_eval_steps += 1
 
    print("  Accuracy: {0:.2f}".format(eval_accuracy/nb_eval_steps))
    # print("  F1: {0:.2f}".format(eval_f1/nb_eval_steps))
    print("  Validation took: {:}".format(format_time(time.time() - t0)))
 
print("")
print("Training complete!")


======== Epoch 1 / 10 ========
Training...

  Average training loss: 1.33
  Training epcoh took: 0:02:03

Running Validation...
  Accuracy: 0.57
  Validation took: 0:00:04

======== Epoch 2 / 10 ========
Training...

  Average training loss: 1.14
  Training epcoh took: 0:02:02

Running Validation...
  Accuracy: 0.57
  Validation took: 0:00:04

======== Epoch 3 / 10 ========
Training...

  Average training loss: 1.01
  Training epcoh took: 0:02:02

Running Validation...
  Accuracy: 0.56
  Validation took: 0:00:04

======== Epoch 4 / 10 ========
Training...

  Average training loss: 0.87
  Training epcoh took: 0:02:02

Running Validation...
  Accuracy: 0.54
  Validation took: 0:00:04

======== Epoch 5 / 10 ========
Training...

  Average training loss: 0.74
  Training epcoh took: 0:02:03

Running Validation...
  Accuracy: 0.56
  Validation took: 0:00:04

======== Epoch 6 / 10 ========
Training...

  Average training loss: 0.62
  Training epcoh took: 0:02:03

Running Validation...
  Accu

**BERT 감정분석 모델 신규 텍스트 함수 선언 ②**

In [54]:
# 문장 테스트
def test_sentences(inputs, masks):
 
    # 평가모드로 변경
    model.eval()
 
    # 문장을 입력 데이터로 변환
    #inputs, masks = convert_input_data(sentences)
    inputs = inputs
    masks = masks
 
    # 데이터를 GPU에 넣음
    b_input_ids = inputs.to(device)
    b_input_mask = masks.to(device)
            
    # 그래디언트 계산 안함
    with torch.no_grad():     
        # Forward 수행
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask)
 
    # 로스 구함
    logits = outputs[0]
 
    # CPU로 데이터 이동
    logits = logits.detach().cpu().numpy()
 
    return logits

**BERT를 이용한 감정분석 모델 테스트 Output 데이터 생성 ②**

- test 데이터 범위 지정 (GPU 사용량 관련 지정) ②

In [55]:
test_kaggle_inputs_1 = test_inputs[:1623]
test_kaggle_masks_1 = test_masks[:1623]

- Kaggle 테스트 데이터로 예측 수행 ②

In [56]:
logits = test_sentences(test_kaggle_inputs_1, test_kaggle_masks_1)
 
x_predict_BERT = []
x_predict_BERT = logits
 
x_predict_BERT_socre = []
x_predict_BERT_socre = np.argmax(logits, axis = 1)
x_predict_BERT_score = x_predict_BERT_socre.tolist()
 
print(x_predict_BERT)
print(x_predict_BERT_score)

[[-0.8769415   6.129223   -1.1356474  ... -1.7227292  -0.2658733
  -1.4541612 ]
 [ 2.000862   -0.05734778 -0.14913087 ... -1.841039    4.3261786
  -1.5999286 ]
 [ 2.1303837   1.3608861  -1.2604394  ...  2.7951014  -0.56876606
  -0.56646067]
 ...
 [-0.9040129   6.319728   -0.93034947 ... -1.7514741  -0.7096881
  -1.2862419 ]
 [-0.9040129   6.319728   -0.93034947 ... -1.7514741  -0.7096881
  -1.2862419 ]
 [ 1.1343977   0.4019394   5.2158365  ... -1.270308   -0.5918013
  -2.421614  ]]
[1, 6, 5, 1, 0, 0, 1, 0, 6, 7, 0, 1, 0, 1, 6, 6, 3, 6, 0, 0, 1, 1, 6, 0, 2, 5, 5, 0, 5, 5, 6, 0, 0, 1, 1, 0, 1, 1, 7, 1, 1, 0, 6, 6, 1, 1, 0, 0, 6, 1, 1, 1, 1, 1, 1, 1, 6, 2, 0, 1, 0, 1, 0, 0, 1, 5, 1, 6, 6, 2, 0, 1, 6, 2, 1, 0, 1, 0, 0, 5, 1, 6, 1, 2, 6, 2, 2, 1, 1, 1, 1, 1, 1, 1, 5, 3, 1, 1, 1, 1, 1, 1, 2, 7, 2, 1, 1, 0, 1, 5, 1, 1, 0, 0, 0, 1, 6, 3, 0, 3, 5, 1, 5, 1, 6, 6, 0, 0, 0, 2, 1, 1, 1, 0, 6, 1, 0, 1, 0, 1, 1, 1, 2, 1, 0, 1, 0, 1, 6, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 6, 6, 2, 6, 5, 0, 3, 1, 0, 6,

- BERT output csv 파일 저장 ②

In [57]:
ensemble_BERT = pd.DataFrame(x_predict_BERT)
print(ensemble_BERT)

             0         1         2  ...         5         6         7
0    -0.876942  6.129223 -1.135647  ... -1.722729 -0.265873 -1.454161
1     2.000862 -0.057348 -0.149131  ... -1.841039  4.326179 -1.599929
2     2.130384  1.360886 -1.260439  ...  2.795101 -0.568766 -0.566461
3     0.237185  6.321426 -1.309232  ... -1.357003 -0.942002 -1.366298
4     2.843277  0.553510  0.321285  ...  1.807672 -2.783490 -0.078807
...        ...       ...       ...  ...       ...       ...       ...
1618  3.344316 -0.301319 -1.741242  ... -1.267917 -0.788039  0.165639
1619  1.159054  1.147098  4.923578  ... -1.778968 -0.160705 -2.593185
1620 -0.904013  6.319728 -0.930349  ... -1.751474 -0.709688 -1.286242
1621 -0.904013  6.319728 -0.930349  ... -1.751474 -0.709688 -1.286242
1622  1.134398  0.401939  5.215837  ... -1.270308 -0.591801 -2.421614

[1623 rows x 8 columns]


In [58]:
ensemble_BERT.to_csv('ensemble_BERT_eng.csv')

- BERT output 레이블 변환 파일 저장 ②

In [62]:
def inttolabel(str):
    return { 0 : 'non-neutral',
             1 : 'neutral', 
             2 : 'joy', 
             3 : 'sadness', 
             4 : 'fear', 
             5 : 'anger', 
             6 : 'surprise', 
             7 : 'disgust'}[str]
 
predicted_BERT_str = []
 
for d in x_predict_BERT_score:
  predicted_BERT_str.append(inttolabel(d))

In [63]:
ensemble_BERT_out = pd.DataFrame({'Expected' : predicted_BERT_str})
print(ensemble_BERT_out)

         Expected
0         neutral
1        surprise
2           anger
3         neutral
4     non-neutral
...           ...
1618  non-neutral
1619          joy
1620      neutral
1621      neutral
1622          joy

[1623 rows x 1 columns]


- Kaggle 리더보드 업로드 파일 생성 (csv 파일 변환 후 다운로드 하여 인덱스 칼럼명 'Id' 입력 필요)

In [64]:
ensemble_BERT_out.to_csv('ensemble_BERT_eng_score.csv')

**앙상블 예측 결과 산출 ③**

In [ ]:
from google.colab import files
files.upload()

Saving ensamble_ELECTRA_eng.csv to ensamble_ELECTRA_eng.csv


{'ensamble_ELECTRA_eng.csv': b',0,1,2,3,4,5,6,7\n0,2.0612762,2.9848442,0.004510751,-2.1855066,-1.9981459,-1.3132193,0.5004205,-2.1679301\n1,1.5568866,0.4431348,2.7816553,-2.9118273,-2.2438114,-1.2314606,1.1533288,-2.191992\n2,2.0247262,1.1826705,-0.6503403,-1.8229717,-1.7525363,0.56938463,-0.27042714,-1.2493104\n3,1.4525363,1.7594435,-1.5505246,0.15951067,-0.56217897,-0.3259243,-0.92219657,-1.2503514\n4,1.2492777,2.9509015,0.4344187,-2.7234905,-1.9319054,-0.47076485,0.332609,-2.527093\n5,1.2733825,-0.79459286,-1.0702616,-0.7125045,-1.0156505,0.18368635,1.2723023,-0.90771717\n6,1.2795843,1.2342179,-1.8920275,-1.3354971,-1.0663849,-0.22227696,1.8318658,-1.5746374\n7,1.1054649,1.7428952,-0.8904261,-2.766032,-1.7117906,-0.19738951,2.24679,-1.8551267\n8,1.7715682,0.5618672,-1.4243257,-2.0004475,-1.0904834,0.4878581,1.0370762,-0.81103307\n9,1.398607,1.5067521,-1.6220305,-2.1680715,-1.0142074,0.19353354,1.3037033,-0.9841827\n10,1.5992148,0.49818352,0.06263328,-2.3708732,-2.0251725,-0.4991295,

- 업로드 ensemble_ELECTRA.csv, ensemble_BERT.csv ③

In [66]:
ensemble_ELECTRA= pd.read_csv("./ensemble_ELECTRA_eng.csv", index_col=0)
ensemble_BERT = pd.read_csv("./ensemble_BERT_eng.csv", index_col=0)
 
print(ensemble_ELECTRA)
print(ensemble_BERT)

             0         1         2  ...         5         6         7
0    -0.165225  9.072702 -2.187644  ... -1.569252 -0.980510 -1.580460
1    -0.475748 -1.141959 -1.247234  ... -1.277070  7.603567 -1.280787
2     4.024747 -3.274255 -2.544062  ...  6.058974 -2.917479  0.214780
3    -0.310701  9.593419 -1.077573  ... -2.743481 -1.569642 -2.049925
4    -0.630141 -1.900750 -1.120545  ...  8.143746 -1.294476 -0.198117
...        ...       ...       ...  ...       ...       ...       ...
1618  4.083575 -0.439334 -3.954473  ... -2.378966 -1.429735  1.858147
1619 -0.481695 -0.882736  8.524299  ... -1.767983 -1.552010 -1.798602
1620 -0.595267  9.256457 -1.090489  ... -1.989375 -0.976490 -1.791849
1621 -0.595267  9.256457 -1.090489  ... -1.989375 -0.976490 -1.791849
1622  8.382175 -1.811585 -0.437499  ... -0.041499 -2.321845 -2.110752

[1623 rows x 8 columns]
             0         1         2  ...         5         6         7
0    -0.876942  6.129223 -1.135647  ... -1.722729 -0.265873 -1.45

- 앙상블 예측결과 Soft Voting ③

In [67]:
# 앙상블 데이터 SUM
ensemble = ensemble_BERT + ensemble_ELECTRA
print(ensemble)
 
# 앙상블 모델 수로 나누어줌
ensemble_out = ensemble / 2
print(ensemble_out)

             0          1          2  ...         5          6         7
0    -1.042166  15.201925  -3.323291  ... -3.291981  -1.246384 -3.034621
1     1.525114  -1.199307  -1.396365  ... -3.118109  11.929746 -2.880716
2     6.155131  -1.913369  -3.804501  ...  8.854076  -3.486245 -0.351680
3    -0.073516  15.914845  -2.386805  ... -4.100484  -2.511644 -3.416223
4     2.213136  -1.347240  -0.799260  ...  9.951418  -4.077966 -0.276923
...        ...        ...        ...  ...       ...        ...       ...
1618  7.427891  -0.740653  -5.695715  ... -3.646883  -2.217774  2.023786
1619  0.677359   0.264361  13.447877  ... -3.546951  -1.712715 -4.391787
1620 -1.499280  15.576185  -2.020838  ... -3.740849  -1.686178 -3.078091
1621 -1.499280  15.576185  -2.020838  ... -3.740849  -1.686178 -3.078091
1622  9.516573  -1.409646   4.778338  ... -1.311807  -2.913646 -4.532366

[1623 rows x 8 columns]
             0         1         2  ...         5         6         7
0    -0.521083  7.600962 -1.6

- 앙상블 예측결과 Soft Voting 결과 산출 ③

In [69]:
ensemble_score = []
ensemble_score = np.array(ensemble_out)
#ensemble_score = np.delete(ensemble_score, 0, axis = 1)
ensemble_score_out = np.argmax(ensemble_score, axis = 1)
ensemble_score_out = ensemble_score_out.tolist()
 
print(ensemble_score_out[:100])
print(np.shape(ensemble_score_out))

[1, 6, 5, 1, 5, 3, 1, 1, 6, 0, 5, 1, 0, 1, 6, 6, 3, 6, 0, 1, 1, 1, 6, 0, 2, 5, 5, 0, 5, 5, 4, 0, 7, 1, 1, 6, 1, 1, 6, 1, 1, 2, 6, 0, 1, 6, 3, 0, 1, 1, 1, 1, 1, 1, 1, 1, 6, 2, 3, 0, 2, 1, 0, 1, 1, 0, 1, 6, 5, 6, 0, 1, 1, 2, 1, 5, 0, 0, 6, 0, 0, 6, 1, 2, 6, 2, 2, 1, 1, 1, 1, 1, 1, 1, 5, 3, 1, 0, 1, 1]
(1623,)


- 앙상블 예측결과 레이블 변환 및 예측결과 산출 ③

In [70]:
def inttolabel(str):
    return { 0 : 'non-neutral',
             1 : 'neutral', 
             2 : 'joy', 
             3 : 'sadness', 
             4 : 'fear', 
             5 : 'anger', 
             6 : 'surprise', 
             7 : 'disgust'}[str]
 
predicted_str = []
 
for d in ensemble_score_out:
  predicted_str.append(inttolabel(d))

In [71]:
print(predicted_str)

['neutral', 'surprise', 'anger', 'neutral', 'anger', 'sadness', 'neutral', 'neutral', 'surprise', 'non-neutral', 'anger', 'neutral', 'non-neutral', 'neutral', 'surprise', 'surprise', 'sadness', 'surprise', 'non-neutral', 'neutral', 'neutral', 'neutral', 'surprise', 'non-neutral', 'joy', 'anger', 'anger', 'non-neutral', 'anger', 'anger', 'fear', 'non-neutral', 'disgust', 'neutral', 'neutral', 'surprise', 'neutral', 'neutral', 'surprise', 'neutral', 'neutral', 'joy', 'surprise', 'non-neutral', 'neutral', 'surprise', 'sadness', 'non-neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'surprise', 'joy', 'sadness', 'non-neutral', 'joy', 'neutral', 'non-neutral', 'neutral', 'neutral', 'non-neutral', 'neutral', 'surprise', 'anger', 'surprise', 'non-neutral', 'neutral', 'neutral', 'joy', 'neutral', 'anger', 'non-neutral', 'non-neutral', 'surprise', 'non-neutral', 'non-neutral', 'surprise', 'neutral', 'joy', 'surprise', 'joy', 'joy', 'neutral', 'neu

In [72]:
ensemble_out = pd.DataFrame({'Expected' : predicted_str})
print(ensemble_out)

         Expected
0         neutral
1        surprise
2           anger
3         neutral
4           anger
...           ...
1618  non-neutral
1619          joy
1620      neutral
1621      neutral
1622  non-neutral

[1623 rows x 1 columns]


- Kaggle 리더보드 업로드 파일 생성 (csv 파일 변환 후 다운로드 하여 인덱스 칼럼명 'Id' 입력 필요)

In [74]:
ensemble_out.to_csv('ensemble_submission.csv')